<a href="https://colab.research.google.com/github/hanane60/Hanane-Rasuli/blob/master/Battle_of_neighborhoods_Week_1_2.ipynb" target="_parent"><img src="https://colab.research.google.com/assets/colab-badge.svg" alt="Open In Colab"/></a>

In [10]:
import os # Operating System
import numpy as np
import pandas as pd
import datetime as dt # Datetime
import json # library to handle JSON files

!conda install -c conda-forge geopy --yes
from geopy.geocoders import Nominatim # convert an address into latitude and longitude values

import requests # library to handle requests
from pandas.io.json import json_normalize # tranform JSON file into a pandas dataframe

# Matplotlib and associated plotting modules
import matplotlib.cm as cm
import matplotlib.colors as colors

!conda install -c conda-forge folium=0.5.0 --yes
import folium #import folium # map rendering library

print('Libraries imported.')

/bin/bash: conda: command not found
/bin/bash: conda: command not found
Libraries imported.


In [0]:
#Read the data for examination (Source: http://landregistry.data.gov.uk/)
df_ppd = pd.read_csv("http://prod2.publicdata.landregistry.gov.uk.s3-website-eu-west-1.amazonaws.com/pp-2018.csv")

In [13]:
df_ppd.head(5)


{666758D7-43A9-3363-E053-6B04A8C0D74E}  405000  2018-01-25 00:00  WR15 8LH  \
0  {666758D7-43AA-3363-E053-6B04A8C0D74E}  315000  2018-01-23 00:00   SY7 8QA   
1  {666758D7-43AD-3363-E053-6B04A8C0D74E}  165000  2018-01-19 00:00   SY1 2BF   
2  {666758D7-43B0-3363-E053-6B04A8C0D74E}  370000  2018-01-22 00:00   SY8 4DF   
3  {666758D7-43B3-3363-E053-6B04A8C0D74E}  320000  2018-01-19 00:00  TF10 7ET   
4  {666758D7-43B4-3363-E053-6B04A8C0D74E}  180000  2018-01-31 00:00   SY3 0NQ   

   D  N  F RAMBLERS WAY Unnamed: 8        Unnamed: 9          BORASTON  \
0  D  N  F  MONT CENISE        NaN               NaN              CLUN   
1  T  Y  F           42        NaN        PENSON WAY               NaN   
2  D  N  F   WILLOW HEY        NaN               NaN  ASHFORD CARBONEL   
3  D  N  F            3        NaN  PRINCESS GARDENS               NaN   
4  S  N  F           79        NaN     LYTHWOOD ROAD      BAYSTON HILL   

  TENBURY WELLS  SHROPSHIRE SHROPSHIRE.1  A A.1  
0   CRAVEN ARMS  SHROPSHIRE   SHROPSHIRE  A   A  
1    SHREWSBURY  SHROPSHIRE   SHROPSHIRE  A   A  
2        LUDLOW  SHROPSHIRE   SHROPSHIRE  A   A  
3       NEWPORT      WREKIN       WREKIN  A   A  
4    SHREWSBURY  SHROPSHIRE   SHROPSHIRE  A   A

In [14]:
df_ppd.shape


(1028554, 16)

In [0]:
# Assign meaningful column names
df_ppd.columns = ['TUID', 'Price', 'Date_Transfer', 'Postcode', 'Prop_Type', 'Old_New', 'Duration', 'PAON', \
                  'SAON', 'Street', 'Locality', 'Town_City', 'District', 'County', 'PPD_Cat_Type', 'Record_Status']

In [0]:
# Format the date column
df_ppd['Date_Transfer'] = df_ppd['Date_Transfer'].apply(pd.to_datetime)

# Delete all obsolete transactions which were done before 2016
df_ppd.drop(df_ppd[df_ppd.Date_Transfer.dt.year < 2016].index, inplace=True)

# Sort by Date of Sale
df_ppd.sort_values(by=['Date_Transfer'],ascending=[False],inplace=True)

In [0]:
df_ppd_london = df_ppd.query("Town_City == 'LONDON'")

# Make a list of street names in LONDON
streets = df_ppd_london['Street'].unique().tolist()

In [0]:
df_grp_price = df_ppd_london.groupby(['Street'])['Price'].mean().reset_index()

# Give meaningful names to the columns
df_grp_price.columns = ['Street', 'Avg_Price']

In [0]:
#Input your Budget's Upper Limit and Lower Limit - Find the locations df_grp_price which fits your budget
df_affordable = df_grp_price.query("(Avg_Price >= 2200000) & (Avg_Price <= 2500000)")

In [20]:
# Display the dataframe
df_affordable

Street     Avg_Price
196                ALBION SQUARE  2.450000e+06
390                  ANHALT ROAD  2.435000e+06
405              ANSDELL TERRACE  2.250000e+06
422              APPLEGARTH ROAD  2.400000e+06
855              BARONSMEAD ROAD  2.375000e+06
981               BEAUCLERC ROAD  2.480000e+06
1102             BELVEDERE DRIVE  2.340000e+06
1215           BICKENHALL STREET  2.208500e+06
1253           BIRCHLANDS AVENUE  2.217000e+06
1553              BRAMPTON GROVE  2.456875e+06
1632           BRIARDALE GARDENS  2.397132e+06
1797                    BROOKWAY  2.400000e+06
1914                BURBAGE ROAD  2.445000e+06
1980                   BURY WALK  2.492500e+06
2068             CALLCOTT STREET  2.375000e+06
2129           CAMPDEN HILL ROAD  2.379653e+06
2136                CAMPION ROAD  2.461000e+06
2158               CANNING PLACE  2.425000e+06
2225               CARLISLE ROAD  2.200000e+06
2230             CARLTON GARDENS  2.483500e+06
2242               CARLYLE COURT  2.300000e+06
2405              CHALCOT SQUARE  2.286679e+06
2483                CHARLES LANE  2.414000e+06
2561            CHELSEA CRESCENT  2.495000e+06
2605         CHESTER CLOSE NORTH  2.450000e+06
2637                CHEYNE COURT  2.250000e+06
2640                  CHEYNE ROW  2.410000e+06
2685               CHISWICK MALL  2.287500e+06
2760                   CITY ROAD  2.468340e+06
2807            CLARENDON STREET  2.250000e+06
2899            CLONCURRY STREET  2.388333e+06
2943                COLBECK MEWS  2.367500e+06
2994            COLLEGE CRESCENT  2.440000e+06
3201       CORNWALL TERRACE MEWS  2.350000e+06
3254          COURT LANE GARDENS  2.360000e+06
3376              CRESCENT GROVE  2.298000e+06
3582               DALEBURY ROAD  2.400000e+06
3847               DEWHURST ROAD  2.425000e+06
3928                  DORIA ROAD  2.362500e+06
3979              DOWNSHIRE HILL  2.225000e+06
4034                DUCHESS WALK  2.477500e+06
4231       ECCLESTON SQUARE MEWS  2.335500e+06
4284               EGBERT STREET  2.265000e+06
4288               EGERTON PLACE  2.200000e+06
4374               ELM PARK ROAD  2.320425e+06
4892               FLORAL STREET  2.227222e+06
5013             FRANK DIXON WAY  2.212500e+06
5095                 FULTON MEWS  2.299000e+06
5238                 GERARD ROAD  2.258500e+06
5241                GERRARD ROAD  2.242500e+06
5286               GIRDLERS ROAD  2.441667e+06
5379         GLOUCESTER CRESCENT  2.350833e+06
5447                GORDON PLACE  2.477000e+06
5483              GRAFTON SQUARE  2.270000e+06
5490              GRAHAM TERRACE  2.325000e+06
5947                HARMAN DRIVE  2.262500e+06
5971               HARRIS STREET  2.471769e+06
6034             HAVANNAH STREET  2.217309e+06
6106              HAZLEWELL ROAD  2.500000e+06
6222               HEREFORD MEWS  2.310000e+06
6242            HERONDALE AVENUE  2.475000e+06
6339        HIGHGATE HIGH STREET  2.211000e+06
6354               HIGHWOOD HILL  2.252500e+06
6390              HILLGATE PLACE  2.200000e+06
6501           HOLLYCROFT AVENUE  2.361375e+06
6505              HOLLYWOOD MEWS  2.350000e+06
6550              HONEYWELL ROAD  2.278333e+06
6606              HORTENSIA ROAD  2.275917e+06
6635               HOXTON SQUARE  2.234286e+06
6661                 HUNTER ROAD  2.300000e+06
6820               JACKSONS LANE  2.362500e+06
6880                 JOHN STREET  2.235000e+06
7185            KINNERTON STREET  2.485600e+06
7219         KNARESBOROUGH PLACE  2.325000e+06
7239                 KNOX STREET  2.250000e+06
7259              LADBROKE GROVE  2.483300e+06
7328              LANCASTER MEWS  2.312500e+06
7399              LANSDOWNE ROAD  2.364876e+06
7427   LATIMER INDUSTRIAL ESTATE  2.400000e+06
7480                LAXTON PLACE  2.500000e+06
7682              LINCOLN AVENUE  2.203500e+06
7711              LINGFIELD ROAD  2.248750e+06
7740               LISSON STREET  2.462500e+06
7774             LIVERPOOL GROVE  2.288000e+06
7866              LONGWOOD DRIV

In [0]:
import pandas as pd
import numpy as np
import datetime as DT
import hmac
from geopy.geocoders import Nominatim
from geopy.distance import vincenty
# import k-means from clustering stage
from sklearn.cluster import KMeans

In [22]:
for index, item in df_affordable.iterrows():
    print(f"index: {index}")
    print(f"item: {item}")
    print(f"item.Street only: {item.Street}")

index: 196
item: Street       ALBION SQUARE
Avg_Price         2.45e+06
Name: 196, dtype: object
item.Street only: ALBION SQUARE
index: 390
item: Street       ANHALT ROAD
Avg_Price      2.435e+06
Name: 390, dtype: object
item.Street only: ANHALT ROAD
index: 405
item: Street       ANSDELL TERRACE
Avg_Price           2.25e+06
Name: 405, dtype: object
item.Street only: ANSDELL TERRACE
index: 422
item: Street       APPLEGARTH ROAD
Avg_Price            2.4e+06
Name: 422, dtype: object
item.Street only: APPLEGARTH ROAD
index: 855
item: Street       BARONSMEAD ROAD
Avg_Price          2.375e+06
Name: 855, dtype: object
item.Street only: BARONSMEAD ROAD
index: 981
item: Street       BEAUCLERC ROAD
Avg_Price          2.48e+06
Name: 981, dtype: object
item.Street only: BEAUCLERC ROAD
index: 1102
item: Street       BELVEDERE DRIVE
Avg_Price           2.34e+06
Name: 1102, dtype: object
item.Street only: BELVEDERE DRIVE
index: 1215
item: Street       BICKENHALL STREET
Avg_Price           2.2085e+06
N

In [23]:
geolocator = Nominatim()


/usr/local/lib/python3.6/dist-packages/geopy/geocoders/osm.py:143: UserWarning: Using Nominatim with the default "geopy/1.17.0" `user_agent` is strongly discouraged, as it violates Nominatim's ToS https://operations.osmfoundation.org/policies/nominatim/ and may possibly cause 403 and 429 HTTP errors. Please specify a custom `user_agent` with `Nominatim(user_agent="my-application")` or by overriding the default `user_agent`: `geopy.geocoders.options.default_user_agent = "my-application"`. In geopy 2.0 this will become an exception.
  UserWarning


In [24]:
df_affordable['city_coord'] = df_affordable['Street'].apply(geolocator.geocode).apply(lambda x: (x.latitude, x.longitude))

/usr/local/lib/python3.6/dist-packages/ipykernel_launcher.py:1: SettingWithCopyWarning: 
A value is trying to be set on a copy of a slice from a DataFrame.
Try using .loc[row_indexer,col_indexer] = value instead

See the caveats in the documentation: http://pandas.pydata.org/pandas-docs/stable/user_guide/indexing.html#returning-a-view-versus-a-copy
  """Entry point for launching an IPython kernel.


In [25]:
df_affordable


Street     Avg_Price  \
196                ALBION SQUARE  2.450000e+06   
390                  ANHALT ROAD  2.435000e+06   
405              ANSDELL TERRACE  2.250000e+06   
422              APPLEGARTH ROAD  2.400000e+06   
855              BARONSMEAD ROAD  2.375000e+06   
981               BEAUCLERC ROAD  2.480000e+06   
1102             BELVEDERE DRIVE  2.340000e+06   
1215           BICKENHALL STREET  2.208500e+06   
1253           BIRCHLANDS AVENUE  2.217000e+06   
1553              BRAMPTON GROVE  2.456875e+06   
1632           BRIARDALE GARDENS  2.397132e+06   
1797                    BROOKWAY  2.400000e+06   
1914                BURBAGE ROAD  2.445000e+06   
1980                   BURY WALK  2.492500e+06   
2068             CALLCOTT STREET  2.375000e+06   
2129           CAMPDEN HILL ROAD  2.379653e+06   
2136                CAMPION ROAD  2.461000e+06   
2158               CANNING PLACE  2.425000e+06   
2225               CARLISLE ROAD  2.200000e+06   
2230             CARLTON GARDENS  2.483500e+06   
2242               CARLYLE COURT  2.300000e+06   
2405              CHALCOT SQUARE  2.286679e+06   
2483                CHARLES LANE  2.414000e+06   
2561            CHELSEA CRESCENT  2.495000e+06   
2605         CHESTER CLOSE NORTH  2.450000e+06   
2637                CHEYNE COURT  2.250000e+06   
2640                  CHEYNE ROW  2.410000e+06   
2685               CHISWICK MALL  2.287500e+06   
2760                   CITY ROAD  2.468340e+06   
2807            CLARENDON STREET  2.250000e+06   
2899            CLONCURRY STREET  2.388333e+06   
2943                COLBECK MEWS  2.367500e+06   
2994            COLLEGE CRESCENT  2.440000e+06   
3201       CORNWALL TERRACE MEWS  2.350000e+06   
3254          COURT LANE GARDENS  2.360000e+06   
3376              CRESCENT GROVE  2.298000e+06   
3582               DALEBURY ROAD  2.400000e+06   
3847               DEWHURST ROAD  2.425000e+06   
3928                  DORIA ROAD  2.362500e+06   
3979              DOWNSHIRE HILL  2.225000e+06   
4034                DUCHESS WALK  2.477500e+06   
4231       ECCLESTON SQUARE MEWS  2.335500e+06   
4284               EGBERT STREET  2.265000e+06   
4288               EGERTON PLACE  2.200000e+06   
4374               ELM PARK ROAD  2.320425e+06   
4892               FLORAL STREET  2.227222e+06   
5013             FRANK DIXON WAY  2.212500e+06   
5095                 FULTON MEWS  2.299000e+06   
5238                 GERARD ROAD  2.258500e+06   
5241                GERRARD ROAD  2.242500e+06   
5286               GIRDLERS ROAD  2.441667e+06   
5379         GLOUCESTER CRESCENT  2.350833e+06   
5447                GORDON PLACE  2.477000e+06   
5483              GRAFTON SQUARE  2.270000e+06   
5490              GRAHAM TERRACE  2.325000e+06   
5947                HARMAN DRIVE  2.262500e+06   
5971               HARRIS STREET  2.471769e+06   
6034             HAVANNAH STREET  2.217309e+06   
6106              HAZLEWELL ROAD  2.500000e+06   
6222               HEREFORD MEWS  2.310000e+06   
6242            HERONDALE AVENUE  2.475000e+06   
6339        HIGHGATE HIGH STREET  2.211000e+06   
6354               HIGHWOOD HILL  2.252500e+06   
6390              HILLGATE PLACE  2.200000e+06   
6501           HOLLYCROFT AVENUE  2.361375e+06   
6505              HOLLYWOOD MEWS  2.350000e+06   
6550              HONEYWELL ROAD  2.278333e+06   
6606              HORTENSIA ROAD  2.275917e+06   
6635               HOXTON SQUARE  2.234286e+06   
6661                 HUNTER ROAD  2.300000e+06   
6820               JACKSONS LANE  2.362500e+06   
6880                 JOHN STREET  2.235000e+06   
7185            KINNERTON STREET  2.485600e+06   
7219         KNARESBOROUGH PLACE  2.325000e+06   
7239                 KNOX STREET  2.250000e+06   
7259              LADBROKE GROVE  2.483300e+06   
7328              LANCASTER MEWS  2.312500e+06   
7399              LANSDOWNE ROAD  2.364876e+06   
7427   LATIMER INDUSTRIAL ESTATE  2.400000e+06   
7480                LAXTON

In [26]:
df_affordable[['Latitude', 'Longitude']] = df_affordable['city_coord'].apply(pd.Series)


/usr/local/lib/python3.6/dist-packages/pandas/core/frame.py:3509: SettingWithCopyWarning: 
A value is trying to be set on a copy of a slice from a DataFrame.
Try using .loc[row_indexer,col_indexer] = value instead

See the caveats in the documentation: http://pandas.pydata.org/pandas-docs/stable/user_guide/indexing.html#returning-a-view-versus-a-copy
  self[k1] = value[k2]


In [27]:
df_affordable


Street     Avg_Price  \
196                ALBION SQUARE  2.450000e+06   
390                  ANHALT ROAD  2.435000e+06   
405              ANSDELL TERRACE  2.250000e+06   
422              APPLEGARTH ROAD  2.400000e+06   
855              BARONSMEAD ROAD  2.375000e+06   
981               BEAUCLERC ROAD  2.480000e+06   
1102             BELVEDERE DRIVE  2.340000e+06   
1215           BICKENHALL STREET  2.208500e+06   
1253           BIRCHLANDS AVENUE  2.217000e+06   
1553              BRAMPTON GROVE  2.456875e+06   
1632           BRIARDALE GARDENS  2.397132e+06   
1797                    BROOKWAY  2.400000e+06   
1914                BURBAGE ROAD  2.445000e+06   
1980                   BURY WALK  2.492500e+06   
2068             CALLCOTT STREET  2.375000e+06   
2129           CAMPDEN HILL ROAD  2.379653e+06   
2136                CAMPION ROAD  2.461000e+06   
2158               CANNING PLACE  2.425000e+06   
2225               CARLISLE ROAD  2.200000e+06   
2230             CARLTON GARDENS  2.483500e+06   
2242               CARLYLE COURT  2.300000e+06   
2405              CHALCOT SQUARE  2.286679e+06   
2483                CHARLES LANE  2.414000e+06   
2561            CHELSEA CRESCENT  2.495000e+06   
2605         CHESTER CLOSE NORTH  2.450000e+06   
2637                CHEYNE COURT  2.250000e+06   
2640                  CHEYNE ROW  2.410000e+06   
2685               CHISWICK MALL  2.287500e+06   
2760                   CITY ROAD  2.468340e+06   
2807            CLARENDON STREET  2.250000e+06   
2899            CLONCURRY STREET  2.388333e+06   
2943                COLBECK MEWS  2.367500e+06   
2994            COLLEGE CRESCENT  2.440000e+06   
3201       CORNWALL TERRACE MEWS  2.350000e+06   
3254          COURT LANE GARDENS  2.360000e+06   
3376              CRESCENT GROVE  2.298000e+06   
3582               DALEBURY ROAD  2.400000e+06   
3847               DEWHURST ROAD  2.425000e+06   
3928                  DORIA ROAD  2.362500e+06   
3979              DOWNSHIRE HILL  2.225000e+06   
4034                DUCHESS WALK  2.477500e+06   
4231       ECCLESTON SQUARE MEWS  2.335500e+06   
4284               EGBERT STREET  2.265000e+06   
4288               EGERTON PLACE  2.200000e+06   
4374               ELM PARK ROAD  2.320425e+06   
4892               FLORAL STREET  2.227222e+06   
5013             FRANK DIXON WAY  2.212500e+06   
5095                 FULTON MEWS  2.299000e+06   
5238                 GERARD ROAD  2.258500e+06   
5241                GERRARD ROAD  2.242500e+06   
5286               GIRDLERS ROAD  2.441667e+06   
5379         GLOUCESTER CRESCENT  2.350833e+06   
5447                GORDON PLACE  2.477000e+06   
5483              GRAFTON SQUARE  2.270000e+06   
5490              GRAHAM TERRACE  2.325000e+06   
5947                HARMAN DRIVE  2.262500e+06   
5971               HARRIS STREET  2.471769e+06   
6034             HAVANNAH STREET  2.217309e+06   
6106              HAZLEWELL ROAD  2.500000e+06   
6222               HEREFORD MEWS  2.310000e+06   
6242            HERONDALE AVENUE  2.475000e+06   
6339        HIGHGATE HIGH STREET  2.211000e+06   
6354               HIGHWOOD HILL  2.252500e+06   
6390              HILLGATE PLACE  2.200000e+06   
6501           HOLLYCROFT AVENUE  2.361375e+06   
6505              HOLLYWOOD MEWS  2.350000e+06   
6550              HONEYWELL ROAD  2.278333e+06   
6606              HORTENSIA ROAD  2.275917e+06   
6635               HOXTON SQUARE  2.234286e+06   
6661                 HUNTER ROAD  2.300000e+06   
6820               JACKSONS LANE  2.362500e+06   
6880                 JOHN STREET  2.235000e+06   
7185            KINNERTON STREET  2.485600e+06   
7219         KNARESBOROUGH PLACE  2.325000e+06   
7239                 KNOX STREET  2.250000e+06   
7259              LADBROKE GROVE  2.483300e+06   
7328              LANCASTER MEWS  2.312500e+06   
7399              LANSDOWNE ROAD  2.364876e+06   
7427   LATIMER INDUSTRIAL ESTATE  2.400000e+06   
7480                LAXTON

In [0]:
df = df_affordable.drop(columns=['city_coord'])


In [29]:
df

Street     Avg_Price   Latitude   Longitude
196                ALBION SQUARE  2.450000e+06 -41.273758  173.289393
390                  ANHALT ROAD  2.435000e+06  51.480316   -0.166801
405              ANSDELL TERRACE  2.250000e+06  51.499890   -0.189103
422              APPLEGARTH ROAD  2.400000e+06  53.748654   -0.326670
855              BARONSMEAD ROAD  2.375000e+06  51.477315   -0.239457
981               BEAUCLERC ROAD  2.480000e+06  30.211452  -81.617981
1102             BELVEDERE DRIVE  2.340000e+06  40.470500  -86.106311
1215           BICKENHALL STREET  2.208500e+06  51.521201   -0.158908
1253           BIRCHLANDS AVENUE  2.217000e+06  51.448394   -0.160468
1553              BRAMPTON GROVE  2.456875e+06  51.589961   -0.318525
1632           BRIARDALE GARDENS  2.397132e+06  51.560175   -0.195431
1797                    BROOKWAY  2.400000e+06  45.432185 -122.802812
1914                BURBAGE ROAD  2.445000e+06  51.448260   -0.088507
1980                   BURY WALK  2.492500e+06  52.145529   -0.423593
2068             CALLCOTT STREET  2.375000e+06  51.508350   -0.198328
2129           CAMPDEN HILL ROAD  2.379653e+06  51.501410   -0.195116
2136                CAMPION ROAD  2.461000e+06  52.681375    0.965471
2158               CANNING PLACE  2.425000e+06  51.499570   -0.184248
2225               CARLISLE ROAD  2.200000e+06  43.399438  -79.973215
2230             CARLTON GARDENS  2.483500e+06 -37.801943  144.971970
2242               CARLYLE COURT  2.300000e+06  32.972701  -97.173392
2405              CHALCOT SQUARE  2.286679e+06  51.541196   -0.155817
2483                CHARLES LANE  2.414000e+06  27.372325  -82.559255
2561            CHELSEA CRESCENT  2.495000e+06  34.522443  -85.443891
2605         CHESTER CLOSE NORTH  2.450000e+06  51.529205   -0.145081
2637                CHEYNE COURT  2.250000e+06  51.599677    0.525623
2640                  CHEYNE ROW  2.410000e+06  51.483717   -0.169603
2685               CHISWICK MALL  2.287500e+06  51.487185   -0.248017
2760                   CITY ROAD  2.468340e+06  51.529697   -0.097763
2807            CLARENDON STREET  2.250000e+06  42.365275  -71.153456
2899            CLONCURRY STREET  2.388333e+06  51.473763   -0.216244
2943                COLBECK MEWS  2.367500e+06  51.492950   -0.185921
2994            COLLEGE CRESCENT  2.440000e+06  37.282334  -76.724918
3201       CORNWALL TERRACE MEWS  2.350000e+06  51.524066   -0.157667
3254          COURT LANE GARDENS  2.360000e+06  51.448500   -0.080102
3376              CRESCENT GROVE  2.298000e+06  46.115586  -60.725330
3582               DALEBURY ROAD  2.400000e+06  51.438268   -0.167669
3847               DEWHURST ROAD  2.425000e+06  51.498737   -0.220666
3928                  DORIA ROAD  2.362500e+06  51.473116   -0.201748
3979              DOWNSHIRE HILL  2.225000e+06  51.555662   -0.170293
4034                DUCHESS WALK  2.477500e+06  51.503801   -0.076921
4231       ECCLESTON SQUARE MEWS  2.335500e+06  51.491785   -0.142260
4284               EGBERT STREET  2.265000e+06  53.507218   -2.190610
4288               EGERTON PLACE  2.200000e+06  51.496687   -0.166950
4374               ELM PARK ROAD  2.320425e+06  51.633987   -0.092524
4892               FLORAL STREET  2.227222e+06  51.513210   -0.122973
5013             FRANK DIXON WAY  2.212500e+06  51.442795   -0.080397
5095                 FULTON MEWS  2.299000e+06  51.512558   -0.184629
5238                 GERARD ROAD  2.258500e+06  51.805800    1.135193
5241                GERRARD ROAD  2.242500e+06  51.533866   -0.101248
5286               GIRDLERS ROAD  2.441667e+06  51.496697   -0.215531
5379         GLOUCESTER CRESCENT  2.350833e+06  49.633823 -118.406686
5447                GORDON PLACE  2.477000e+06 -41.166498  146.346358
5483              GRAFTON SQUARE  2.270000e+06  51.463966   -0.139084
5490              GRAHAM TERRACE  2.325000e+06  51.491547   -0.154275
5947                HARMAN DRIVE  2.262500e+06  51.558738   -0.206307
5971               HARRIS STREET  2.

In [30]:
address = 'London, UK'

geolocator = Nominatim()
location = geolocator.geocode(address)
latitude = location.latitude
longitude = location.longitude
print('The geograpical coordinate of London City are {}, {}.'.format(latitude, longitude))

/usr/local/lib/python3.6/dist-packages/geopy/geocoders/osm.py:143: UserWarning: Using Nominatim with the default "geopy/1.17.0" `user_agent` is strongly discouraged, as it violates Nominatim's ToS https://operations.osmfoundation.org/policies/nominatim/ and may possibly cause 403 and 429 HTTP errors. Please specify a custom `user_agent` with `Nominatim(user_agent="my-application")` or by overriding the default `user_agent`: `geopy.geocoders.options.default_user_agent = "my-application"`. In geopy 2.0 this will become an exception.
  UserWarning


The geograpical coordinate of London City are 51.5073219, -0.1276474.


In [31]:
# create map of London using latitude and longitude values
map_london = folium.Map(location=[latitude, longitude], zoom_start=11)

# add markers to map
for lat, lng, price, street in zip(df['Latitude'], df['Longitude'], df['Avg_Price'], df['Street']):
    label = '{}, {}'.format(street, price)
    label = folium.Popup(label, parse_html=True)
    folium.CircleMarker(
        [lat, lng],
        radius=5,
        popup=label,
        color='blue',
        fill=True,
        fill_color='#3186cc',
        fill_opacity=0.7,
        parse_html=False).add_to(map_london)  
    
map_london

In [32]:
#Define Foursquare Credentials and Version

CLIENT_ID = 'KI3TR0QO4JOKMFELOMF3WSOOI3HFNBF5YLW354MYWBKDHEX3' # Foursquare ID
CLIENT_SECRET = 'QF4ZBLJRBV4BQX52DVWUPEHJ14A2UJABPCZARZQZYTKIISUD' # Foursquare Secret
VERSION = '20181206' # Foursquare API version

print('Your credentails:')
print('CLIENT_ID: ' + CLIENT_ID)
print('CLIENT_SECRET:' + CLIENT_SECRET)

Your credentails:
CLIENT_ID: KI3TR0QO4JOKMFELOMF3WSOOI3HFNBF5YLW354MYWBKDHEX3
CLIENT_SECRET:QF4ZBLJRBV4BQX52DVWUPEHJ14A2UJABPCZARZQZYTKIISUD


In [0]:
def getNearbyVenues(names, latitudes, longitudes, radius=500, LIMIT=100):
    
    venues_list=[]
    for name, lat, lng in zip(names, latitudes, longitudes):
        print(name)
            
        # create the API request URL
        url = 'https://api.foursquare.com/v2/venues/explore?&client_id={}&client_secret={}&v={}&ll={},{}&radius={}&limit={}'.format(
            CLIENT_ID, 
            CLIENT_SECRET, 
            VERSION, 
            lat, 
            lng, 
            radius, 
            LIMIT)
            
        # make the GET request
        results = requests.get(url).json()["response"]['groups'][0]['items']
        
        # return only relevant information for each nearby venue
        venues_list.append([(
            name, 
            lat, 
            lng, 
            v['venue']['name'], 
            v['venue']['location']['lat'], 
            v['venue']['location']['lng'],  
            v['venue']['categories'][0]['name']) for v in results])

    nearby_venues = pd.DataFrame([item for venue_list in venues_list for item in venue_list])
    nearby_venues.columns = ['Street', 
                  'Street Latitude', 
                  'Street Longitude', 
                  'Venue', 
                  'Venue Latitude', 
                  'Venue Longitude', 
                  'Venue Category']
    
    return(nearby_venues)

In [34]:
# Run the above function on each location and create a new dataframe called location_venues and display it.
location_venues = getNearbyVenues(names=df['Street'],
                                   latitudes=df['Latitude'],
                                   longitudes=df['Longitude']
                                  )

ALBION SQUARE
ANHALT ROAD
ANSDELL TERRACE
APPLEGARTH ROAD
BARONSMEAD ROAD
BEAUCLERC ROAD
BELVEDERE DRIVE
BICKENHALL STREET
BIRCHLANDS AVENUE
BRAMPTON GROVE
BRIARDALE GARDENS
BROOKWAY
BURBAGE ROAD
BURY WALK
CALLCOTT STREET
CAMPDEN HILL ROAD
CAMPION ROAD
CANNING PLACE
CARLISLE ROAD
CARLTON GARDENS
CARLYLE COURT
CHALCOT SQUARE
CHARLES LANE
CHELSEA CRESCENT
CHESTER CLOSE NORTH
CHEYNE COURT
CHEYNE ROW
CHISWICK MALL
CITY ROAD
CLARENDON STREET
CLONCURRY STREET
COLBECK MEWS
COLLEGE CRESCENT
CORNWALL TERRACE MEWS
COURT LANE GARDENS
CRESCENT GROVE
DALEBURY ROAD
DEWHURST ROAD
DORIA ROAD
DOWNSHIRE HILL
DUCHESS WALK
ECCLESTON SQUARE MEWS
EGBERT STREET
EGERTON PLACE
ELM PARK ROAD
FLORAL STREET
FRANK DIXON WAY
FULTON MEWS
GERARD ROAD
GERRARD ROAD
GIRDLERS ROAD
GLOUCESTER CRESCENT
GORDON PLACE
GRAFTON SQUARE
GRAHAM TERRACE
HARMAN DRIVE
HARRIS STREET
HAVANNAH STREET
HAZLEWELL ROAD
HEREFORD MEWS
HERONDALE AVENUE
HIGHGATE HIGH STREET
HIGHWOOD HILL
HILLGATE PLACE
HOLLYCROFT AVENUE
HOLLYWOOD MEWS
HONEYWELL

In [35]:
location_venues


Street  Street Latitude  Street Longitude  \
0                 ALBION SQUARE       -41.273758        173.289393   
1                 ALBION SQUARE       -41.273758        173.289393   
2                 ALBION SQUARE       -41.273758        173.289393   
3                 ALBION SQUARE       -41.273758        173.289393   
4                 ALBION SQUARE       -41.273758        173.289393   
5                 ALBION SQUARE       -41.273758        173.289393   
6                 ALBION SQUARE       -41.273758        173.289393   
7                 ALBION SQUARE       -41.273758        173.289393   
8                 ALBION SQUARE       -41.273758        173.289393   
9                 ALBION SQUARE       -41.273758        173.289393   
10                ALBION SQUARE       -41.273758        173.289393   
11                ALBION SQUARE       -41.273758        173.289393   
12                ALBION SQUARE       -41.273758        173.289393   
13                ALBION SQUARE       -41.273758        173.289393   
14                ALBION SQUARE       -41.273758        173.289393   
15                ALBION SQUARE       -41.273758        173.289393   
16                ALBION SQUARE       -41.273758        173.289393   
17                ALBION SQUARE       -41.273758        173.289393   
18                ALBION SQUARE       -41.273758        173.289393   
19                ALBION SQUARE       -41.273758        173.289393   
20                ALBION SQUARE       -41.273758        173.289393   
21                ALBION SQUARE       -41.273758        173.289393   
22                ALBION SQUARE       -41.273758        173.289393   
23                ALBION SQUARE       -41.273758        173.289393   
24                ALBION SQUARE       -41.273758        173.289393   
25                ALBION SQUARE       -41.273758        173.289393   
26                ALBION SQUARE       -41.273758        173.289393   
27                  ANHALT ROAD        51.480316         -0.166801   
28                  ANHALT ROAD        51.480316         -0.166801   
29                  ANHALT ROAD        51.480316         -0.166801   
30                  ANHALT ROAD        51.480316         -0.166801   
31                  ANHALT ROAD        51.480316         -0.166801   
32                  ANHALT ROAD        51.480316         -0.166801   
33                  ANHALT ROAD        51.480316         -0.166801   
34                  ANHALT ROAD        51.480316         -0.166801   
35                  ANHALT ROAD        51.480316         -0.166801   
36                  ANHALT ROAD        51.480316         -0.166801   
37                  ANHALT ROAD        51.480316         -0.166801   
38                  ANHALT ROAD        51.480316         -0.166801   
39                  ANHALT ROAD        51.480316         -0.166801   
40                  ANHALT ROAD        51.480316         -0.166801   
41                  ANHALT ROAD        51.480316         -0.166801   
42              ANSDELL TERRACE        51.499890         -0.189103   
43              ANSDELL TERRACE        51.499890         -0.189103   
44              ANSDELL TERRACE        51.499890         -0.189103   
45              ANSDELL TERRACE        51.499890         -0.189103   
46              ANSDELL TERRACE        51.499890         -0.189103   
47              ANSDELL TERRACE        51.499890         -0.189103   
48              ANSDELL TERRACE        51.499890         -0.189103   
49              ANSDELL TERRACE        51.499890         -0.189103   
50              ANSDELL TERRACE        51.499890         -0.189103   
51              ANSDELL TERRACE        51.499890         -0.189103   
52              ANSDELL TERRACE        51.499890         -0.189103   
53              ANSDELL TERRACE        51.499890         -0.189103   
54              ANSDELL TERRACE        51.499890         -0.189103   
55              ANSDELL TERRACE        51.499890         -0.189103   
56              ANSDELL TERRACE    

In [36]:
location_venues.groupby('Street').count()

Street Latitude  Street Longitude  Venue  \
Street                                                                
ALBION SQUARE                           27                27     27   
ANHALT ROAD                             15                15     15   
ANSDELL TERRACE                         44                44     44   
APPLEGARTH ROAD                          4                 4      4   
BARONSMEAD ROAD                         13                13     13   
BEAUCLERC ROAD                           4                 4      4   
BELVEDERE DRIVE                         33                33     33   
BICKENHALL STREET                       90                90     90   
BIRCHLANDS AVENUE                       10                10     10   
BRAMPTON GROVE                           1                 1      1   
BRIARDALE GARDENS                        6                 6      6   
BURBAGE ROAD                            11                11     11   
BURY WALK                               14                14     14   
CALLCOTT STREET                         50                50     50   
CAMPDEN HILL ROAD                       58                58     58   
CAMPION ROAD                             2                 2      2   
CANNING PLACE                           32                32     32   
CARLTON GARDENS                         63                63     63   
CARLYLE COURT                            1                 1      1   
CHALCOT SQUARE                          51                51     51   
CHESTER CLOSE NORTH                     24                24     24   
CHEYNE COURT                             1                 1      1   
CHEYNE ROW                              57                57     57   
CHISWICK MALL                            5                 5      5   
CITY ROAD                               27                27     27   
CLARENDON STREET                        29                29     29   
CLONCURRY STREET                        31                31     31   
COLBECK MEWS                           100               100    100   
COLLEGE CRESCENT                        16                16     16   
CORNWALL TERRACE MEWS                   63                63     63   
COURT LANE GARDENS                      13                13     13   
CRESCENT GROVE                           1                 1      1   
DALEBURY ROAD                            6                 6      6   
DEWHURST ROAD                           34                34     34   
DORIA ROAD                              64                64     64   
DOWNSHIRE HILL                          38                38     38   
DUCHESS WALK                           100               100    100   
ECCLESTON SQUARE MEWS                  100               100    100   
EGBERT STREET                            2                 2      2   
EGERTON PLACE                          100               100    100   
ELM PARK ROAD                            8                 8      8   
FLORAL STREET                          100               100    100   
FRANK DIXON WAY                          7                 7      7   
FULTON MEWS                             90                90     90   
GERARD ROAD                              6                 6      6   
GERRARD ROAD                           100               100    100   
GIRDLERS ROAD                           35                35     35   
GORDON PLACE                             1                 1      1   
GRAFTON SQUARE                          85                85     85   
GRAHAM TERRACE                          79                79     79   
HARMAN DRIVE                             4                 4      4   
HARRIS STREET                            9                 9      9   
HAVANNAH STREET                         37                37     37   
HAZLEWELL ROAD                           9                 9      9   
HEREFORD MEWS                          100         

In [37]:
# get the List of Unique Categories
print('There are {} uniques categories.'.format(len(location_venues['Venue Category'].unique())))

There are 355 uniques categories.


In [38]:
location_venues.shape


(5706, 7)

In [39]:
# one hot encoding
venues_onehot = pd.get_dummies(location_venues[['Venue Category']], prefix="", prefix_sep="")

# add street column back to dataframe
venues_onehot['Street'] = location_venues['Street'] 

# move street column to the first column
fixed_columns = [venues_onehot.columns[-1]] + list(venues_onehot.columns[:-1])

#fixed_columns
venues_onehot = venues_onehot[fixed_columns]

venues_onehot.head()

Street  Accessories Store  Adult Boutique  Afghan Restaurant  \
0  ALBION SQUARE                  0               0                  0   
1  ALBION SQUARE                  0               0                  0   
2  ALBION SQUARE                  0               0                  0   
3  ALBION SQUARE                  0               0                  0   
4  ALBION SQUARE                  0               0                  0   

   African Restaurant  American Restaurant  Antique Shop  Arcade  \
0                   0                    0             0       0   
1                   0                    0             0       0   
2                   0                    0             0       0   
3                   0                    0             0       0   
4                   0                    0             0       0   

   Argentinian Restaurant  Art Gallery  Art Museum  Arts & Crafts Store  \
0                       0            0           0                    0   
1                       0            0           0                    0   
2                       0            0           0                    0   
3                       0            0           0                    0   
4                       0            0           0                    0   

   Asian Restaurant  Athletics & Sports  Australian Restaurant  \
0                 0                   0                      0   
1                 0                   0                      0   
2                 0                   0                      0   
3                 0                   0                      0   
4                 0                   0                      0   

   Austrian Restaurant  Automotive Shop  BBQ Joint  Baby Store  \
0                    0                0          0           0   
1                    0                0          0           0   
2                    0                0          0           0   
3                    0                0          0           0   
4                    0                0          0           0   

   Badminton Court  Bagel Shop  Bakery  Bank  Bar  Baseball Field  Bay  Beach  \
0                0           0       0     0    1               0    0      0   
1                0           0       0     0    0               0    0      0   
2                0           0       0     0    0               0    0      0   
3                0           0       0     0    0               0    0      0   
4                0           0       0     0    0               0    0      0   

   Bed & Breakfast  Beer Bar  Beer Garden  Beer Store  Belgian Restaurant  \
0                0         0            0           0                   0   
1                0         0            0           0                   0   
2                0         0            0           0                   0   
3                0         0            0           0                   0   
4                0         0            0           0                   0   

   Big Box Store  Bike Rental / Bike Share  Bike Shop  Bistro  Boarding House  \
0              0                         0          0       0               0   
1              0                         0          0       0               0   
2              0                         0          0       0               0   
3              0                         0          0       0               0   
4              0                         0          0       0               0   

   Boat or Ferry  Bookstore  Botanical Garden  Boutique  Bowling Alley  \
0              0          0                 0         0              0   
1              0          0                 0         0              0   
2              0          0                 0         0              0   
3              0          0                 0         0              0   
4              0          0                 0         0              0   

   Boxing Gym  Brasserie  Bra

In [40]:
london_grouped = venues_onehot.groupby('Street').mean().reset_index()
london_grouped

Street  Accessories Store  Adult Boutique  \
0                ALBION SQUARE           0.000000            0.00   
1                  ANHALT ROAD           0.000000            0.00   
2              ANSDELL TERRACE           0.000000            0.00   
3              APPLEGARTH ROAD           0.000000            0.00   
4              BARONSMEAD ROAD           0.000000            0.00   
5               BEAUCLERC ROAD           0.000000            0.00   
6              BELVEDERE DRIVE           0.030303            0.00   
7            BICKENHALL STREET           0.000000            0.00   
8            BIRCHLANDS AVENUE           0.000000            0.00   
9               BRAMPTON GROVE           0.000000            0.00   
10           BRIARDALE GARDENS           0.000000            0.00   
11                BURBAGE ROAD           0.000000            0.00   
12                   BURY WALK           0.000000            0.00   
13             CALLCOTT STREET           0.000000            0.00   
14           CAMPDEN HILL ROAD           0.000000            0.00   
15                CAMPION ROAD           0.000000            0.00   
16               CANNING PLACE           0.000000            0.00   
17             CARLTON GARDENS           0.000000            0.00   
18               CARLYLE COURT           0.000000            0.00   
19              CHALCOT SQUARE           0.000000            0.00   
20         CHESTER CLOSE NORTH           0.000000            0.00   
21                CHEYNE COURT           0.000000            0.00   
22                  CHEYNE ROW           0.017544            0.00   
23               CHISWICK MALL           0.000000            0.00   
24                   CITY ROAD           0.000000            0.00   
25            CLARENDON STREET           0.000000            0.00   
26            CLONCURRY STREET           0.000000            0.00   
27                COLBECK MEWS           0.000000            0.00   
28            COLLEGE CRESCENT           0.000000            0.00   
29       CORNWALL TERRACE MEWS           0.015873            0.00   
30          COURT LANE GARDENS           0.000000            0.00   
31              CRESCENT GROVE           0.000000            0.00   
32               DALEBURY ROAD           0.000000            0.00   
33               DEWHURST ROAD           0.000000            0.00   
34                  DORIA ROAD           0.000000            0.00   
35              DOWNSHIRE HILL           0.000000            0.00   
36                DUCHESS WALK           0.000000            0.00   
37       ECCLESTON SQUARE MEWS           0.000000            0.00   
38               EGBERT STREET           0.000000            0.00   
39               EGERTON PLACE           0.000000            0.00   
40               ELM PARK ROAD           0.000000            0.00   
41               FLORAL STREET           0.000000            0.00   
42             FRANK DIXON WAY           0.000000            0.00   
43                 FULTON MEWS           0.000000            0.00   
44                 GERARD ROAD           0.000000            0.00   
45                GERRARD ROAD           0.000000            0.00   
46               GIRDLERS ROAD           0.000000            0.00   
47                GORDON PLACE           0.000000            0.00   
48              GRAFTON SQUARE           0.000000            0.00   
49              GRAHAM TERRACE           0.000000            0.00   
50                HARMAN DRIVE           0.000000            0.00   
51               HARRIS STREET           0.000000            0.00   
52             HAVANNAH STREET           0.000000            0.00   
53              HAZLEWELL ROAD           0.000000            0.00   
54               HEREFORD MEWS           0.000000            0.00   
55            HERONDALE AVENUE           0.000000            0.00   
56        HIGHGATE HIGH STREET           0.000000            0.00   
57               HIGHW

In [41]:
london_grouped.shape

(148, 356)

In [42]:
# What are the top 5 venues/facilities nearby profitable real estate investments?#

num_top_venues = 5

for hood in london_grouped['Street']:
    print("----"+hood+"----")
    temp = london_grouped[london_grouped['Street'] == hood].T.reset_index()
    temp.columns = ['venue','freq']
    temp = temp.iloc[1:]
    temp['freq'] = temp['freq'].astype(float)
    temp = temp.round({'freq': 2})
    print(temp.sort_values('freq', ascending=False).reset_index(drop=True).head(num_top_venues))
    print('\n')

----ALBION SQUARE----
         venue  freq
0         Café  0.22
1   Restaurant  0.07
2          Bar  0.07
3          Pub  0.07
4  Coffee Shop  0.07


----ANHALT ROAD----
                 venue  freq
0                  Pub  0.27
1        Grocery Store  0.13
2  Japanese Restaurant  0.07
3         Cocktail Bar  0.07
4    French Restaurant  0.07


----ANSDELL TERRACE----
               venue  freq
0         Restaurant  0.09
1     Clothing Store  0.09
2                Pub  0.07
3              Hotel  0.07
4  Indian Restaurant  0.05


----APPLEGARTH ROAD----
              venue  freq
0               Bar  0.25
1               Pub  0.25
2            Casino  0.25
3         Nightclub  0.25
4  Ramen Restaurant  0.00


----BARONSMEAD ROAD----
                 venue  freq
0    Food & Drink Shop  0.15
1        Movie Theater  0.08
2  Indie Movie Theater  0.08
3       Farmers Market  0.08
4                 Park  0.08


----BEAUCLERC ROAD----
                  venue  freq
0       Harbor / Marina  0.50
1

In [0]:
# Define a function to return the most common venues/facilities nearby real estate investments#

def return_most_common_venues(row, num_top_venues):
    row_categories = row.iloc[1:]
    row_categories_sorted = row_categories.sort_values(ascending=False)
    
    return row_categories_sorted.index.values[0:num_top_venues]

In [0]:
num_top_venues = 10

indicators = ['st', 'nd', 'rd']

# create columns according to number of top venues
columns = ['Street']
for ind in np.arange(num_top_venues):
    try:
        columns.append('{}{} Most Common Venue'.format(ind+1, indicators[ind]))
    except:
        columns.append('{}th Most Common Venue'.format(ind+1))

In [0]:
# create a new dataframe
venues_sorted = pd.DataFrame(columns=columns)
venues_sorted['Street'] = london_grouped['Street']

for ind in np.arange(london_grouped.shape[0]):
    venues_sorted.iloc[ind, 1:] = return_most_common_venues(london_grouped.iloc[ind, :], num_top_venues)

In [46]:
venues_sorted.head()


Street 1st Most Common Venue 2nd Most Common Venue  \
0    ALBION SQUARE                  Café            Restaurant   
1      ANHALT ROAD                   Pub         Grocery Store   
2  ANSDELL TERRACE            Restaurant        Clothing Store   
3  APPLEGARTH ROAD                   Pub                Casino   
4  BARONSMEAD ROAD     Food & Drink Shop   Indie Movie Theater   

  3rd Most Common Venue 4th Most Common Venue 5th Most Common Venue  \
0     Indian Restaurant                   Pub                   Bar   
1  Gym / Fitness Center                 Plaza          Cocktail Bar   
2                   Pub                 Hotel     Indian Restaurant   
3             Nightclub                   Bar           Film Studio   
4       Thai Restaurant                   Pub           Pizza Place   

  6th Most Common Venue 7th Most Common Venue 8th Most Common Venue  \
0           Coffee Shop     French Restaurant               Brewery   
1                 Diner    English Restaurant     Outdoor Sculpture   
2             Juice Bar    Italian Restaurant    English Restaurant   
3           Fabric Shop               Factory    Falafel Restaurant   
4            Restaurant           Coffee Shop                  Park   

     9th Most Common Venue 10th Most Common Venue  
0  New American Restaurant      Fish & Chips Shop  
1                   Garden      French Restaurant  
2                     Café      French Restaurant  
3                     Farm         Farmers Market  
4           Farmers Market        Nature Preserve

In [47]:
venues_sorted.shape


(148, 11)

In [48]:
london_grouped.shape


(148, 356)

In [0]:
london_grouped=df


In [50]:
#Distribute in 5 Clusters

# set number of clusters
kclusters = 5

london_grouped_clustering = london_grouped.drop('Street', 1)

# run k-means clustering
kmeans = KMeans(n_clusters=kclusters, random_state=0).fit(london_grouped_clustering)

# check cluster labels generated for each row in the dataframe
kmeans.labels_[0:50]

array([1, 4, 2, 4, 3, 1, 3, 2, 2, 1, 4, 4, 1, 1, 3, 3, 1, 4, 2, 1, 0, 0,
       4, 1, 1, 2, 4, 0, 1, 2, 4, 3, 4, 3, 3, 0, 4, 4, 3, 2, 1, 3, 0, 2,
       0, 2, 2, 0, 2, 2], dtype=int32)

In [51]:
#Dataframe to include Clusters

london_grouped_clustering=df
london_grouped_clustering.head()

Street  Avg_Price   Latitude   Longitude
196    ALBION SQUARE  2450000.0 -41.273758  173.289393
390      ANHALT ROAD  2435000.0  51.480316   -0.166801
405  ANSDELL TERRACE  2250000.0  51.499890   -0.189103
422  APPLEGARTH ROAD  2400000.0  53.748654   -0.326670
855  BARONSMEAD ROAD  2375000.0  51.477315   -0.239457

In [52]:
london_grouped_clustering.shape


(162, 4)

In [53]:
df.shape


(162, 4)

In [54]:
london_grouped_clustering.dtypes


Street        object
Avg_Price    float64
Latitude     float64
Longitude    float64
dtype: object

In [55]:
df.dtypes


Street        object
Avg_Price    float64
Latitude     float64
Longitude    float64
dtype: object

In [56]:
# add clustering labels
london_grouped_clustering['Cluster Labels'] = kmeans.labels_

# merge london_grouped with london_data to add latitude/longitude for each neighborhood
london_grouped_clustering = london_grouped_clustering.join(venues_sorted.set_index('Street'), on='Street')

london_grouped_clustering.head(30) # check the last columns!

Street     Avg_Price   Latitude   Longitude  \
196         ALBION SQUARE  2.450000e+06 -41.273758  173.289393   
390           ANHALT ROAD  2.435000e+06  51.480316   -0.166801   
405       ANSDELL TERRACE  2.250000e+06  51.499890   -0.189103   
422       APPLEGARTH ROAD  2.400000e+06  53.748654   -0.326670   
855       BARONSMEAD ROAD  2.375000e+06  51.477315   -0.239457   
981        BEAUCLERC ROAD  2.480000e+06  30.211452  -81.617981   
1102      BELVEDERE DRIVE  2.340000e+06  40.470500  -86.106311   
1215    BICKENHALL STREET  2.208500e+06  51.521201   -0.158908   
1253    BIRCHLANDS AVENUE  2.217000e+06  51.448394   -0.160468   
1553       BRAMPTON GROVE  2.456875e+06  51.589961   -0.318525   
1632    BRIARDALE GARDENS  2.397132e+06  51.560175   -0.195431   
1797             BROOKWAY  2.400000e+06  45.432185 -122.802812   
1914         BURBAGE ROAD  2.445000e+06  51.448260   -0.088507   
1980            BURY WALK  2.492500e+06  52.145529   -0.423593   
2068      CALLCOTT STREET  2.375000e+06  51.508350   -0.198328   
2129    CAMPDEN HILL ROAD  2.379653e+06  51.501410   -0.195116   
2136         CAMPION ROAD  2.461000e+06  52.681375    0.965471   
2158        CANNING PLACE  2.425000e+06  51.499570   -0.184248   
2225        CARLISLE ROAD  2.200000e+06  43.399438  -79.973215   
2230      CARLTON GARDENS  2.483500e+06 -37.801943  144.971970   
2242        CARLYLE COURT  2.300000e+06  32.972701  -97.173392   
2405       CHALCOT SQUARE  2.286679e+06  51.541196   -0.155817   
2483         CHARLES LANE  2.414000e+06  27.372325  -82.559255   
2561     CHELSEA CRESCENT  2.495000e+06  34.522443  -85.443891   
2605  CHESTER CLOSE NORTH  2.450000e+06  51.529205   -0.145081   
2637         CHEYNE COURT  2.250000e+06  51.599677    0.525623   
2640           CHEYNE ROW  2.410000e+06  51.483717   -0.169603   
2685        CHISWICK MALL  2.287500e+06  51.487185   -0.248017   
2760            CITY ROAD  2.468340e+06  51.529697   -0.097763   
2807     CLARENDON STREET  2.250000e+06  42.365275  -71.153456   

      Cluster Labels 1st Most Common Venue   2nd Most Common Venue  \
196                1                  Café              Restaurant   
390                4                   Pub           Grocery Store   
405                2            Restaurant          Clothing Store   
422                4                   Pub                  Casino   
855                3     Food & Drink Shop     Indie Movie Theater   
981                1       Harbor / Marina         Automotive Shop   
1102               3        Clothing Store              Shoe Store   
1215               2                 Hotel             Coffee Shop   
1253               2                   Pub          Breakfast Spot   
1553               1          Home Service                     Zoo   
1632               4    Italian Restaurant     Sporting Goods Shop   
1797               4                   NaN                     NaN   
1914               1                   Pub             Art Gallery   
1980               1           Supermarket      English Restaurant   
2068               3                   Pub           Grocery Store   
2129               3                  Café          Clothing Store   
2136               1          Soccer Field                Windmill   
2158               4                 Hotel              Restaurant   
2225               2                   NaN                     NaN   
2230               1    Italian Restaurant            Dessert Shop   
2242               0                  Farm                     Zoo   
2405               0                  Café      Italian Restaurant   
2483               4                   NaN                     NaN   
2561               1                   NaN                     NaN   
2605               1                Garden    Gym / Fitness Center   
2637               2             Gastropub                     Zoo   
2640               4                  Café      Italian Restaurant   
2685        

In [57]:
# Create Map

map_clusters = folium.Map(location=[latitude, longitude], zoom_start=11)

# set color scheme for the clusters
x = np.arange(kclusters)
ys = [i+x+(i*x)**2 for i in range(kclusters)]
colors_array = cm.rainbow(np.linspace(0, 1, len(ys)))
rainbow = [colors.rgb2hex(i) for i in colors_array]

# add markers to the map
markers_colors = []
for lat, lon, poi, cluster in zip(london_grouped_clustering['Latitude'], london_grouped_clustering['Longitude'], london_grouped_clustering['Street'], london_grouped_clustering['Cluster Labels']):
    label = folium.Popup(str(poi) + ' Cluster ' + str(cluster), parse_html=True)
    folium.CircleMarker(
        [lat, lon],
        radius=5,
        popup=label,
        color=rainbow[cluster-1],
        fill=True,
        fill_color=rainbow[cluster-1],
        fill_opacity=0.7).add_to(map_clusters)
       
map_clusters

In [58]:
london_grouped_clustering.loc[london_grouped_clustering['Cluster Labels'] == 0, london_grouped_clustering.columns[[1] + list(range(5, london_grouped_clustering.shape[1]))]].head()


Avg_Price 1st Most Common Venue 2nd Most Common Venue  \
2242  2.300000e+06                  Farm                   Zoo   
2405  2.286679e+06                  Café    Italian Restaurant   
2685  2.287500e+06               Brewery                   Pub   
3376  2.298000e+06                 Hotel                   Zoo   
4284  2.265000e+06                   Pub     Convenience Store   

     3rd Most Common Venue 4th Most Common Venue 5th Most Common Venue  \
2242       Coworking Space           Fabric Shop               Factory   
2405                   Bar           Coffee Shop                   Pub   
2685             Reservoir            Art Museum             Gift Shop   
3376     Fish & Chips Shop           Fabric Shop               Factory   
4284     Fish & Chips Shop           Fabric Shop               Factory   

     6th Most Common Venue 7th Most Common Venue 8th Most Common Venue  \
2242    Falafel Restaurant        Farmers Market  Fast Food Restaurant   
2405                  Park     French Restaurant           Pizza Place   
2685     Fish & Chips Shop               Factory    Falafel Restaurant   
3376    Falafel Restaurant                  Farm        Farmers Market   
4284    Falafel Restaurant                  Farm        Farmers Market   

     9th Most Common Venue 10th Most Common Venue  
2242   Filipino Restaurant            Film Studio  
2405             Bookstore         Breakfast Spot  
2685                  Farm         Farmers Market  
3376  Fast Food Restaurant    Filipino Restaurant  
4284  Fast Food Restaurant    Filipino Restaurant

In [59]:
london_grouped_clustering.loc[london_grouped_clustering['Cluster Labels'] == 1, london_grouped_clustering.columns[[1] + list(range(5, london_grouped_clustering.shape[1]))]].head()

Avg_Price 1st Most Common Venue 2nd Most Common Venue  \
196   2450000.0                  Café            Restaurant   
981   2480000.0       Harbor / Marina       Automotive Shop   
1553  2456875.0          Home Service                   Zoo   
1914  2445000.0                   Pub           Art Gallery   
1980  2492500.0           Supermarket    English Restaurant   

     3rd Most Common Venue 4th Most Common Venue 5th Most Common Venue  \
196      Indian Restaurant                   Pub                   Bar   
981            Pizza Place                   Zoo           Film Studio   
1553           Event Space           Fabric Shop               Factory   
1914         Grocery Store                Bakery             Gastropub   
1980                   Pub        Hardware Store           Dry Cleaner   

     6th Most Common Venue 7th Most Common Venue 8th Most Common Venue  \
196            Coffee Shop     French Restaurant               Brewery   
981            Fabric Shop               Factory    Falafel Restaurant   
1553    Falafel Restaurant                  Farm        Farmers Market   
1914               Stadium           Pizza Place    Athletics & Sports   
1980  Fast Food Restaurant                  Café           Coffee Shop   

        9th Most Common Venue 10th Most Common Venue  
196   New American Restaurant      Fish & Chips Shop  
981                      Farm         Farmers Market  
1553     Fast Food Restaurant    Filipino Restaurant  
1914        Food & Drink Shop         Cricket Ground  
1980                     Park    Rental Car Location

In [60]:
london_grouped_clustering.loc[london_grouped_clustering['Cluster Labels'] == 2, london_grouped_clustering.columns[[1] + list(range(5, london_grouped_clustering.shape[1]))]].head()

Avg_Price 1st Most Common Venue 2nd Most Common Venue  \
405   2250000.0            Restaurant        Clothing Store   
1215  2208500.0                 Hotel           Coffee Shop   
1253  2217000.0                   Pub        Breakfast Spot   
2225  2200000.0                   NaN                   NaN   
2637  2250000.0             Gastropub                   Zoo   

     3rd Most Common Venue 4th Most Common Venue 5th Most Common Venue  \
405                    Pub                 Hotel     Indian Restaurant   
1215                  Café    Italian Restaurant             Gastropub   
1253           Coffee Shop     French Restaurant    Chinese Restaurant   
2225                   NaN                   NaN                   NaN   
2637     Fish & Chips Shop           Fabric Shop               Factory   

     6th Most Common Venue 7th Most Common Venue 8th Most Common Venue  \
405              Juice Bar    Italian Restaurant    English Restaurant   
1215           Pizza Place    Chinese Restaurant            Restaurant   
1253                Bakery         Train Station                  Lake   
2225                   NaN                   NaN                   NaN   
2637    Falafel Restaurant                  Farm        Farmers Market   

     9th Most Common Venue 10th Most Common Venue  
405                   Café      French Restaurant  
1215       Thai Restaurant          Movie Theater  
1253               Brewery     Dim Sum Restaurant  
2225                   NaN                    NaN  
2637  Fast Food Restaurant    Filipino Restaurant

In [61]:
london_grouped_clustering.loc[london_grouped_clustering['Cluster Labels'] == 3, london_grouped_clustering.columns[[1] + list(range(5, london_grouped_clustering.shape[1]))]].head()

Avg_Price 1st Most Common Venue 2nd Most Common Venue  \
855   2375000.0     Food & Drink Shop   Indie Movie Theater   
1102  2340000.0        Clothing Store            Shoe Store   
2068  2375000.0                   Pub         Grocery Store   
2129  2379652.7                  Café        Clothing Store   
2943  2367500.0                 Hotel                   Pub   

     3rd Most Common Venue   4th Most Common Venue 5th Most Common Venue  \
855        Thai Restaurant                     Pub           Pizza Place   
1102        Cosmetics Shop  Furniture / Home Store        Lingerie Store   
2068           Pizza Place                    Park    Italian Restaurant   
2129    Italian Restaurant       French Restaurant    English Restaurant   
2943                Garden                    Café           Coffee Shop   

     6th Most Common Venue       7th Most Common Venue 8th Most Common Venue  \
855             Restaurant                 Coffee Shop                  Park   
1102     Accessories Store           Mobile Phone Shop    Miscellaneous Shop   
2068           Yoga Studio                        Café                 Hotel   
2129          Burger Joint  Modern European Restaurant                Bakery   
2943    Italian Restaurant          Chinese Restaurant                   Bar   

         9th Most Common Venue 10th Most Common Venue  
855             Farmers Market        Nature Preserve  
1102        Mexican Restaurant              Bookstore  
2068         Indian Restaurant                 Hostel  
2129               Art Gallery             Restaurant  
2943  Mediterranean Restaurant             Restaurant

In [62]:
london_grouped_clustering.loc[london_grouped_clustering['Cluster Labels'] == 4, london_grouped_clustering.columns[[1] + list(range(5, london_grouped_clustering.shape[1]))]].head()

Avg_Price 1st Most Common Venue 2nd Most Common Venue  \
390   2435000.0                   Pub         Grocery Store   
422   2400000.0                   Pub                Casino   
1632  2397132.0    Italian Restaurant   Sporting Goods Shop   
1797  2400000.0                   NaN                   NaN   
2158  2425000.0                 Hotel            Restaurant   

     3rd Most Common Venue 4th Most Common Venue 5th Most Common Venue  \
390   Gym / Fitness Center                 Plaza          Cocktail Bar   
422              Nightclub                   Bar           Film Studio   
1632  Gym / Fitness Center     Convenience Store         Grocery Store   
1797                   NaN                   NaN                   NaN   
2158    Chinese Restaurant                   Pub    Italian Restaurant   

     6th Most Common Venue 7th Most Common Venue 8th Most Common Venue  \
390                  Diner    English Restaurant     Outdoor Sculpture   
422            Fabric Shop               Factory    Falafel Restaurant   
1632           Coffee Shop                   Zoo           Film Studio   
1797                   NaN                   NaN                   NaN   
2158        Clothing Store                   Bar     French Restaurant   

     9th Most Common Venue 10th Most Common Venue  
390                 Garden      French Restaurant  
422                   Farm         Farmers Market  
1632               Factory     Falafel Restaurant  
1797                   NaN                    NaN  
2158            Hookah Bar          Grocery Store